In [33]:
import numpy as np
import pandas as pd
from rdkit import Chem
from rdkit.Chem import AllChem
import py3Dmol
import Bio.PDB

In [34]:
def parse_pdb(file_path):
    """
    Parse a PDB file and return the protein and ligand atoms.
    

    Args:
        file_path (str): The path to the PDB file to parse.

    Returns:
        tuple: A tuple containing:
            - list: A list of tuples containing the protein atoms. Each tuple contains the atom type, x, y, z, chain, and residue number.
            - list: A list of tuples containing the ligand atoms. Each tuple contains the atom type, x, y, and z.
    """
    protein_atoms = []
    ligand_atoms = []

    amino_acids = {}
    current_chain = None

    with open(file_path, 'r') as pdb_file:
        for line in pdb_file:
            if line.startswith("ATOM"):
                atom_type = line[12:16].strip()
                x = float(line[30:38])
                y = float(line[38:46])
                z = float(line[46:54])
                chain = line[21]
                residue_number = int(line[22:26])
                residue_name = line[17:20]

                if chain != current_chain:
                    amino_acids = {}
                    current_chain = chain

                if chain not in amino_acids:
                    amino_acids[chain] = {}

                amino_acids[chain][residue_number] = residue_name

                protein_atoms.append((atom_type, x, y, z, chain, residue_number))

            elif line.startswith("HETATM"):
                atom_type = line[12:16].strip()
                x = float(line[30:38])
                y = float(line[38:46])
                z = float(line[46:54])

                ligand_atoms.append((atom_type, x, y, z))
                print(ligand_atoms)
                print(protein_atoms)
                print(amino_acids)
    return protein_atoms, ligand_atoms, amino_acids


In [35]:
def calculate_distances(protein_atoms, ligand_atoms):
    distances = []

    for protein_atom in protein_atoms:
       # print("Example protein atom:", protein_atom)  # Debug print
        for ligand_atom in ligand_atoms:
           # print("Example ligand atom:", ligand_atom)  # Debug print
            dist = np.sqrt((protein_atom[1] - ligand_atom[1]) ** 2 +
                           (protein_atom[2] - ligand_atom[2]) ** 2 +
                           (protein_atom[3] - ligand_atom[3]) ** 2)
            distances.append((protein_atom[0], ligand_atom[0], dist, protein_atom[4], protein_atom[5]))

    return distances

In [36]:
def sort_distances(distances):
    return sorted(distances, key=lambda x: x[2])

In [37]:
def write_to_excel(sorted_distances, output_file='distances.xlsx'):
    df = pd.DataFrame(sorted_distances, columns=['Protein Atom', 'Ligand Atom', 'Distance', 'Chain', 'Residue Number'])
    df.to_excel(output_file, index=False)
    print(f"Distances written to {output_file}")

In [38]:
def find_hydrogen_bonds(sorted_distances):
    hydrogen_bonds = []

    for protein_atom_type, ligand_atom_type, dist, chain, residue_number in sorted_distances:
        if (protein_atom_type[0] in ['N', 'O', 'S'] and ligand_atom_type[0] in ['N', 'O', 'S']) or \
                (ligand_atom_type[0] in ['N', 'O', 'S'] and protein_atom_type[0] in ['N', 'O', 'S']):
            if 2.7 <= dist <= 3.3:  # Adjust the threshold distance for hydrogen bonds
                hydrogen_bonds.append((chain, residue_number, protein_atom_type, ligand_atom_type, dist))

    if hydrogen_bonds:
        print("\nPossible Hydrogen Bond Interactions:")
        for bond in hydrogen_bonds:
            print(bond)
    else:
        print("\nNo possible Hydrogen Bond Interactions found.")

    return hydrogen_bonds

In [39]:
def visualize_ligand_sticks_with_labels(ligand_atoms, hydrogen_bonds, amino_acids, protein_atoms):
    # Create a Py3Dmol view
    view = py3Dmol.view(width=800, height=600)

    # Create a PDB file string for ligand atoms
    pdb_string = ""
    for i, (atom_type, x, y, z) in enumerate(ligand_atoms):
        pdb_string += f"ATOM  {i+1:<5} {atom_type:<4} MOL     1    {x:>8.3f}{y:>8.3f}{z:>8.3f}\n"

    # Add ligand atoms from the PDB file string
    view.addModel(pdb_string, "pdb")

    # Set style to stick representation for ligand atoms
    view.setStyle({'stick': {}})

    # Add labels to ligand atoms
    for i, (atom_type, x, y, z) in enumerate(ligand_atoms):
        view.addLabel(atom_type, {'position': {'x': x, 'y': y, 'z': z}})

    # Add light blue spheres for hydrogen atoms
    hydrogen_atoms = [atom for atom in ligand_atoms if atom[0].startswith('H')]
    for i, (atom_type, x, y, z) in enumerate(hydrogen_atoms):
        view.addSphere({'center': {'x': x, 'y': y, 'z': z}, 'radius': 0.3, 'color': 'lightblue'})

     # Add protein atoms as red spheres and label them
    for chain, residue_number, protein_atom_type, ligand_atom_type, dist in hydrogen_bonds:
        amino_acid = amino_acids.get(chain, {}).get(residue_number, "Unknown")
        # Find the coordinates of the protein atom involved in the hydrogen bond
        protein_atom_coords = next((x, y, z) for _, x, y, z, ch, rn in protein_atoms if ch == chain and rn == residue_number)
        # Add red sphere for the protein atom
        view.addSphere({'center': {'x': protein_atom_coords[0], 'y': protein_atom_coords[1], 'z': protein_atom_coords[2]}, 'radius': 0.3, 'color': 'red'})
        # Label the protein atom with amino acid and residue number
        label_text = f"{amino_acid} {residue_number}({chain})"
        view.addLabel(label_text, {'position': {'x': protein_atom_coords[0], 'y': protein_atom_coords[1], 'z': protein_atom_coords[2]}})
         
    # Add yellow dotted lines between ligand atoms involved in hydrogen bonds
    for chain, residue_number, protein_atom_type, ligand_atom_type, dist in hydrogen_bonds:
        # Find the coordinates of the ligand atom involved in the hydrogen bond
        ligand_atom_coords = None
        for atom in ligand_atoms:
            if atom[0] == ligand_atom_type:
                ligand_atom_coords = atom[1:4]
                break
        if ligand_atom_coords:
            # Find the coordinates of the protein atom involved in the hydrogen bond
            protein_atom_coords = None
            for _, x, y, z, ch, rn in protein_atoms:
                if ch == chain and rn == residue_number:
                    protein_atom_coords = (x, y, z)
                    break
            if protein_atom_coords:
                # Add yellow dotted line between ligand atom and protein atom
        
               # Define the number of segments for the line
                num_segments = 10
                
                # Calculate the length of each segment
                segment_length = dist / num_segments
                
                # Add yellow dotted line between ligand atom and protein atom with increased thickness using cylinder shape
                for i in range(num_segments):
                    start_pos = {'x': ligand_atom_coords[0] + (protein_atom_coords[0] - ligand_atom_coords[0]) * i / num_segments,
                                 'y': ligand_atom_coords[1] + (protein_atom_coords[1] - ligand_atom_coords[1]) * i / num_segments,
                                 'z': ligand_atom_coords[2] + (protein_atom_coords[2] - ligand_atom_coords[2]) * i / num_segments}
                    end_pos = {'x': ligand_atom_coords[0] + (protein_atom_coords[0] - ligand_atom_coords[0]) * (i + 0.5) / num_segments,
                               'y': ligand_atom_coords[1] + (protein_atom_coords[1] - ligand_atom_coords[1]) * (i + 0.5) / num_segments,
                               'z': ligand_atom_coords[2] + (protein_atom_coords[2] - ligand_atom_coords[2]) * (i + 0.5) / num_segments}
                    view.addCylinder({'start': start_pos, 'end': end_pos, 'radius': 0.07, 'color': 'yellow'})


    # Set background color to black
    view.setBackgroundColor('black')

    # Zoom to fit the structure
    view.zoomTo()

    # Show the 3D view
    view.show()

In [40]:
pdb_file_path = r"sample_data\first.pdb"

protein_atoms, ligand_atoms, amino_acids = parse_pdb(pdb_file_path)
distances = calculate_distances(protein_atoms, ligand_atoms)
sorted_distances = sort_distances(distances)

[('C1', -23.328, 14.678, -32.36)]
[('N', -58.403, 8.243, -23.592, 'A', 50), ('H1', -58.735, 7.356, -23.913, 'A', 50), ('H2', -58.33, 8.23, -22.595, 'A', 50), ('H3', -59.043, 8.959, -23.87, 'A', 50), ('CA', -57.091, 8.511, -24.173, 'A', 50), ('CB', -57.162, 8.41, -25.709, 'A', 50), ('CG', -55.79, 8.231, -26.375, 'A', 50), ('CD', -55.883, 8.43, -27.891, 'A', 50), ('NE', -54.8, 7.744, -28.605, 'A', 50), ('HE', -54.416, 6.925, -28.178, 'A', 50), ('CZ', -54.281, 8.124, -29.784, 'A', 50), ('NH1', -54.632, 9.272, -30.379, 'A', 50), ('1HH1', -55.3, 9.876, -29.945, 'A', 50), ('2HH1', -54.226, 9.525, -31.257, 'A', 50), ('NH2', -53.396, 7.33, -30.387, 'A', 50), ('1HH2', -53.128, 6.466, -29.961, 'A', 50), ('2HH2', -53.0, 7.599, -31.265, 'A', 50), ('C', -56.573, 9.871, -23.685, 'A', 50), ('O', -56.798, 10.9, -24.324, 'A', 50), ('N', -55.912, 9.872, -22.519, 'A', 51), ('H', -55.719, 8.989, -22.091, 'A', 51), ('CA', -55.455, 11.078, -21.832, 'A', 51), ('CB', -55.209, 10.741, -20.351, 'A', 51), ('CG',

In [41]:
# write_to_excel(sorted_distances, output_file='sorted_distances.xlsx')

In [42]:
# Finding and printing possible hydrogen bonds
hydrogen_bonds = find_hydrogen_bonds(sorted_distances)
if hydrogen_bonds:
    print("\nPossible Hydrogen Bond Interactions:")
    for chain, residue_number, protein_atom_type, ligand_atom_type, dist in hydrogen_bonds:
        amino_acid = amino_acids.get(chain, {}).get(residue_number, "Unknown")
        print(f"{amino_acid} {residue_number}({chain}){protein_atom_type}(donor) ------ {ligand_atom_type}(acceptor)   {dist}")
else:
    print("\nNo possible Hydrogen Bond Interactions found.")



Possible Hydrogen Bond Interactions:
('A', 151, 'O', 'N1', 2.718914673173837)
('A', 153, 'N', 'O2', 3.078475109530692)
('A', 153, 'OG', 'O2', 3.162595611202927)

Possible Hydrogen Bond Interactions:
GLY 151(A)O(donor) ------ N1(acceptor)   2.718914673173837
SER 153(A)N(donor) ------ O2(acceptor)   3.078475109530692
SER 153(A)OG(donor) ------ O2(acceptor)   3.162595611202927


In [43]:
# Call visualize_ligand_sticks_with_labels with ligand_atoms, hydrogen_bonds, protein_atoms, and amino_acids
visualize_ligand_sticks_with_labels(ligand_atoms, hydrogen_bonds, amino_acids, protein_atoms)


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

In [44]:
pdb_file_path = "sample_data/first.pdb"

protein_atoms, ligand_atoms, amino_acids = parse_pdb(pdb_file_path)
distances = calculate_distances(protein_atoms, ligand_atoms)
sorted_distances = sort_distances(distances)

[('C1', -23.328, 14.678, -32.36)]
[('N', -58.403, 8.243, -23.592, 'A', 50), ('H1', -58.735, 7.356, -23.913, 'A', 50), ('H2', -58.33, 8.23, -22.595, 'A', 50), ('H3', -59.043, 8.959, -23.87, 'A', 50), ('CA', -57.091, 8.511, -24.173, 'A', 50), ('CB', -57.162, 8.41, -25.709, 'A', 50), ('CG', -55.79, 8.231, -26.375, 'A', 50), ('CD', -55.883, 8.43, -27.891, 'A', 50), ('NE', -54.8, 7.744, -28.605, 'A', 50), ('HE', -54.416, 6.925, -28.178, 'A', 50), ('CZ', -54.281, 8.124, -29.784, 'A', 50), ('NH1', -54.632, 9.272, -30.379, 'A', 50), ('1HH1', -55.3, 9.876, -29.945, 'A', 50), ('2HH1', -54.226, 9.525, -31.257, 'A', 50), ('NH2', -53.396, 7.33, -30.387, 'A', 50), ('1HH2', -53.128, 6.466, -29.961, 'A', 50), ('2HH2', -53.0, 7.599, -31.265, 'A', 50), ('C', -56.573, 9.871, -23.685, 'A', 50), ('O', -56.798, 10.9, -24.324, 'A', 50), ('N', -55.912, 9.872, -22.519, 'A', 51), ('H', -55.719, 8.989, -22.091, 'A', 51), ('CA', -55.455, 11.078, -21.832, 'A', 51), ('CB', -55.209, 10.741, -20.351, 'A', 51), ('CG',

In [45]:
# Write sorted distances to an Excel file
# write_to_excel(sorted_distances, output_file='sorted_distances.xlsx')


In [46]:
# Finding and printing possible hydrogen bonds
hydrogen_bonds = find_hydrogen_bonds(sorted_distances)
if hydrogen_bonds:
    print("\nPossible Hydrogen Bond Interactions:")
    for chain, residue_number, protein_atom_type, ligand_atom_type, dist in hydrogen_bonds:
        amino_acid = amino_acids.get(chain, {}).get(residue_number, "Unknown")
        print(f"{amino_acid} {residue_number}({chain}){protein_atom_type}(donor) ------ {ligand_atom_type}(acceptor)   {dist}")
else:
    print("\nNo possible Hydrogen Bond Interactions found.")


Possible Hydrogen Bond Interactions:
('A', 151, 'O', 'N1', 2.718914673173837)
('A', 153, 'N', 'O2', 3.078475109530692)
('A', 153, 'OG', 'O2', 3.162595611202927)

Possible Hydrogen Bond Interactions:
GLY 151(A)O(donor) ------ N1(acceptor)   2.718914673173837
SER 153(A)N(donor) ------ O2(acceptor)   3.078475109530692
SER 153(A)OG(donor) ------ O2(acceptor)   3.162595611202927


In [47]:
# Call visualize_ligand_sticks_with_labels with ligand_atoms, hydrogen_bonds, protein_atoms, and amino_acids
visualize_ligand_sticks_with_labels(ligand_atoms, hydrogen_bonds, amino_acids, protein_atoms)

3Dmol.js failed to load for some reason. Please check your browser console for error messages.